### fix the UKMO missing Januarys

In [45]:
!pwd

/home/nicolasf/research/Smart_Ideas/code/pre-processors/notebooks/CDS


problem: 

All the T2M forecasts for years 1993 to 2006 are missing the month of January 

These can be however downloaded individually using the CDS download form, but xarray / cfgrib is unable to read them ... 

error message

ECCODES ERROR   :  Unable to find template localDefinition from grib1/local.98.12.def 

this notebook attempts to do this using pygrib 

In [1]:
%matplotlib inline

In [2]:
from matplotlib import pyplot as plt

In [3]:
import pathlib

In [4]:
from datetime import datetime
from dateutil.relativedelta import relativedelta

In [5]:
import pandas as pd 

In [6]:
import xarray as xr

In [7]:
HOME = pathlib.Path.home()

In [8]:
dpath = HOME / 'research' / 'Smart_Ideas' / 'data' / 'GCMs' / 'GRIB' / 'UKMO'

In [9]:
dpath

PosixPath('/home/nicolasf/research/Smart_Ideas/data/GCMs/GRIB/UKMO')

In [10]:
d_vars = {}
d_vars['PRECIP'] = 'tprate'
d_vars['T2M'] = 't2m'
d_vars['SST'] = 'sst'
d_vars['Z850'] = 'z'
d_vars['Z500'] = 'z'

In [11]:
year = 1994

In [14]:
lfiles = list(dpath.rglob(f"*{year}_01.grib"))

In [15]:
lfiles

[PosixPath('/home/nicolasf/research/Smart_Ideas/data/GCMs/GRIB/UKMO/PRECIP/UKMO_system_12_13_14_PRECIP_1994_01.grib'),
 PosixPath('/home/nicolasf/research/Smart_Ideas/data/GCMs/GRIB/UKMO/T2M/UKMO_system_12_13_14_T2M_1994_01.grib')]

In [16]:
for fname in lfiles: 
    try:
        dset = xr.open_dataset(fname, engine='cfgrib', backend_kwargs={'indexpath':''})
        print(dset.info)
        dset.close()
    except: 
        print(f"unable to open {str(fname)}\n")
        pass

unable to open /home/nicolasf/research/Smart_Ideas/data/GCMs/GRIB/UKMO/PRECIP/UKMO_system_12_13_14_PRECIP_1994_01.grib

unable to open /home/nicolasf/research/Smart_Ideas/data/GCMs/GRIB/UKMO/T2M/UKMO_system_12_13_14_T2M_1994_01.grib



### Solution for opening the faulty UKMO 2018 grib files with xarray

In [24]:
c = 'T2M'

### the month of Feb can be read without issue 

In [40]:
dset = xr.open_dataset(f'/home/nicolasf/research/Smart_Ideas/data/GCMs/GRIB/UKMO/{var_name}/UKMO_system_12_13_14_{var_name}_1994_02.grib', engine='cfgrib', backend_kwargs={'indexpath':''})

In [41]:
dset

<xarray.Dataset>
Dimensions:     (latitude: 180, longitude: 360, number: 28, step: 5)
Coordinates:
  * number      (number) int64 0 1 2 3 4 5 6 7 8 ... 19 20 21 22 23 24 25 26 27
    time        datetime64[ns] ...
  * step        (step) timedelta64[ns] 59 days 89 days ... 150 days 181 days
    surface     int64 ...
  * latitude    (latitude) float64 89.5 88.5 87.5 86.5 ... -87.5 -88.5 -89.5
  * longitude   (longitude) float64 0.5 1.5 2.5 3.5 ... 356.5 357.5 358.5 359.5
    valid_time  (step) datetime64[ns] ...
Data variables:
    t2m         (number, step, latitude, longitude) float32 ...
Attributes:
    GRIB_edition:            1
    GRIB_centre:             egrr
    GRIB_centreDescription:  U.K. Met Office - Exeter
    GRIB_subCentre:          98
    Conventions:             CF-1.7
    institution:             U.K. Met Office - Exeter
    history:                 2019-12-20T10:34:29 GRIB to CDM+CF via cfgrib-0....

In [43]:
dset_01 = xr.open_dataset(f'/home/nicolasf/research/Smart_Ideas/data/GCMs/GRIB/UKMO/{var_name}/UKMO_system_12_13_14_{var_name}_1994_01.grib', engine='cfgrib', \
                       backend_kwargs={"indexpath":"", 'filter_by_keys':{'longitudeOfFirstGridPointInDegrees': 0.5}})

In [44]:
dset_01

<xarray.Dataset>
Dimensions:     (latitude: 180, longitude: 360, number: 28, step: 5)
Coordinates:
  * number      (number) int64 0 1 2 3 4 5 6 7 8 ... 19 20 21 22 23 24 25 26 27
    time        datetime64[ns] ...
  * step        (step) timedelta64[ns] 59 days 90 days ... 151 days 181 days
    surface     int64 ...
  * latitude    (latitude) float64 89.5 88.5 87.5 86.5 ... -87.5 -88.5 -89.5
  * longitude   (longitude) float64 0.5 1.5 2.5 3.5 ... 356.5 357.5 358.5 359.5
    valid_time  (step) datetime64[ns] ...
Data variables:
    t2m         (number, step, latitude, longitude) float32 ...
Attributes:
    GRIB_edition:            1
    GRIB_centre:             egrr
    GRIB_centreDescription:  U.K. Met Office - Exeter
    GRIB_subCentre:          98
    Conventions:             CF-1.7
    institution:             U.K. Met Office - Exeter
    history:                 2019-12-20T10:35:43 GRIB to CDM+CF via cfgrib-0....